# Parking Pricing Models Analysis

This notebook explores different dynamic pricing models for parking lots based on real-time data.

* * *
### Installing Necessary Libraries and Dependencies
* * *

First, we'll install the required libraries, primarily `bokeh` for visualization.

In [1]:
!pip install bokeh

* * *
### Importing Libraries
* * *

Now, import the standard data manipulation and visualization libraries.

In [2]:
import numpy as np
import pandas as pd
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource, LinearAxis, Range1d, Legend
from bokeh.layouts import column
from bokeh.palettes import Category10

output_notebook()

* * *
### Loading the Dataset
* * *

Load the parking data from the CSV file into a pandas DataFrame.

In [3]:
df = pd.read_csv('dataset.csv')

### Data Preview

In [4]:
display(df.head())

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172         61         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172         64         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172         80         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172        107         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172        150        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low            1             0      04-10-2016   
1                    low            1             0      04-10-2016   
2                    low            2             0      04-10-2016   
3                    low            2             0      04-10-2016   
4                    low            2             0      04-10-2016   

  LastUpdatedTime  
0        07:59:00  
1        08:25:00  
2        08:59:00  
3        09:32:00  
4        09:59:00

* * *
### Model 1: Simple Occupancy-Based Pricing
* * *

This model adjusts the price based solely on the current occupancy ratio of a parking lot. The price increases as the occupancy increases.

**Formula:** `Price = Base Price + Alpha * (Occupancy / Capacity)`

### Define Base Price and Alpha

In [5]:
BASE_PRICE_M1 = 10.0  # Base price in dollars
ALPHA_M1 = 5.0       # Sensitivity of price to occupancy

### Calculate Model 1 Price

In [6]:
# Get capacity for each lot (assuming capacity is constant per SystemCodeNumber)
capacity_dict = df.groupby('SystemCodeNumber')['Capacity'].first().to_dict()

# Calculate Model 1 price
df['Capacity'] = df['SystemCodeNumber'].map(capacity_dict)
df['OccupancyRatio'] = df['Occupancy'] / df['Capacity']
df['Price_Model1'] = BASE_PRICE_M1 + ALPHA_M1 * df['OccupancyRatio']

### Preview Model 1 Prices

In [7]:
df[['SystemCodeNumber', 'LastUpdatedDate', 'LastUpdatedTime', 'Occupancy', 'Capacity', 'Price_Model1']].head(15)

SystemCodeNumber LastUpdatedDate LastUpdatedTime  Occupancy  Capacity  \
0       BHMBCCMKT01      04-10-2016        07:59:00         61       577   
1       BHMBCCMKT01      04-10-2016        08:25:00         64       577   
2       BHMBCCMKT01      04-10-2016        08:59:00         80       577   
3       BHMBCCMKT01      04-10-2016        09:32:00        107       577   
4       BHMBCCMKT01      04-10-2016        09:59:00        150       577   
5       BHMBCCMKT01      04-10-2016        10:26:00        177       577   
6       BHMBCCMKT01      04-10-2016        10:59:00        219       577   
7       BHMBCCMKT01      04-10-2016        11:25:00        247       577   
8       BHMBCCMKT01      04-10-2016        11:59:00        259       577   
9       BHMBCCMKT01      04-10-2016        12:29:00        266       577   
10      BHMBCCMKT01      04-10-2016        13:02:00        269       577   
11      BHMBCCMKT01      04-10-2016        13:29:00        263       577   
12      BHMBCCMKT01      04-10-2016        14:02:00        238       577   
13      BHMBCCMKT01      04-10-2016        14:29:00        215       577   
14      BHMBCCMKT01      04-10-2016        14:57:00        192       577   

    Price_Model1  
0      10.528596  
1      10.554593  
2      10.693241  
3      10.927210  
4      11.299827  
5      11.533795  
6      11.897747  
7      12.140381  
8      12.244367  
9      12.305026  
10     12.331023  
11     12.279029  
12     12.062392  
13     11.863085  
14     11.663778

* * *
### Model 2: Feature-Rich Demand Model
* * *

This model incorporates multiple factors to estimate "demand" and adjusts the price based on this calculated demand.

Factors include:
- Occupancy Ratio
- Queue Length
- Traffic Condition Nearby
- Is Special Day
- Vehicle Type (weighted)

The raw demand is calculated and then normalized per parking lot before determining the price.

### Prepare Data for Model 2

In [8]:
df_model2 = df.copy()

# Combine date and time into Timestamp
df_model2['Timestamp'] = pd.to_datetime(
    df_model2['LastUpdatedDate'] + ' ' + df_model2['LastUpdatedTime'],
    dayfirst=True
)

# Map categorical features to numerical values
traffic_map = {'low': 0, 'average': 1, 'high': 2}
df_model2['TrafficLevel'] = df_model2['TrafficConditionNearby'].map(traffic_map)

vehicle_weights = {'car': 1.0, 'bike': 0.5, 'truck': 1.5, 'cycle': 0.3}
df_model2['VehicleTypeWeight'] = df_model2['VehicleType'].map(vehicle_weights)

### Define Model 2 Parameters and Calculate Demand

In [9]:
# Define weights for each factor (tuned based on analysis)
alpha_m2 = 1.5    # OccupancyRatio
beta_m2 = 2.5     # QueueLength
gamma_m2 = 0.5    # TrafficLevel (penalty)
delta_m2 = -1.0   # IsSpecialDay (slight negative impact on demand)
epsilon_m2 = 0.1  # VehicleTypeWeight (optional, very weak)

# Compute Raw Demand
df_model2['RawDemand'] = (
    alpha_m2 * df_model2['OccupancyRatio']
  + beta_m2 * df_model2['QueueLength']
  - gamma_m2 * df_model2['TrafficLevel']
  + delta_m2 * df_model2['IsSpecialDay']
  + epsilon_m2 * df_model2['VehicleTypeWeight']
)

### Normalize Demand per Parking Lot

In [10]:
df_model2['NormalizedDemand'] = df_model2.groupby('SystemCodeNumber')['RawDemand'].transform(
    lambda x: (x - x.min()) / (x.max() - x.min() + 1e-6)
)

### Calculate Model 2 Price

In [11]:
BASE_PRICE_M2 = 10
LAMBDA_M2 = 1.0  # how much normalized demand affects price

df_model2['Price_Model2'] = BASE_PRICE_M2 * (1 + LAMBDA_M2 * df_model2['NormalizedDemand'])

# Optional: Clip price to reasonable bounds
df_model2['Price_Model2'] = df_model2['Price_Model2'].clip(lower=5, upper=20)

### Preview Model 2 Prices

In [12]:
df_model2[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'QueueLength', 'TrafficLevel', 'IsSpecialDay', 'NormalizedDemand', 'Price_Model2']].head(10)

SystemCodeNumber           Timestamp  Occupancy  QueueLength  TrafficLevel  \
0      BHMBCCMKT01 2016-10-04 07:59:00         61            1             0   
1      BHMBCCMKT01 2016-10-04 08:25:00         64            1             0   
2      BHMBCCMKT01 2016-10-04 08:59:00         80            2             0   
3      BHMBCCMKT01 2016-10-04 09:32:00        107            2             0   
4      BHMBCCMKT01 2016-10-04 09:59:00        150            2             0   
5      BHMBCCMKT01 2016-10-04 10:26:00        177            3             0   
6      BHMBCCMKT01 2016-10-04 10:59:00        219            6             2   
7      BHMBCCMKT01 2016-10-04 11:25:00        247            5             1   
8      BHMBCCMKT01 2016-10-04 11:59:00        259            5             1   
9      BHMBCCMKT01 2016-10-04 12:29:00        266            8             2   

   IsSpecialDay  NormalizedDemand  Price_Model2  
0             0          0.136529     11.365295  
1             0          0.136817     11.368170  
2             0          0.230516     12.305159  
3             0          0.233104     12.331035  
4             0          0.235381     12.353813  
5             0          0.331978     13.319777  
6             0          0.577476     15.774765  
7             0          0.504584     15.045843  
8             0          0.503154     15.031537  
9             0          0.762625     17.626252

* * *
### Model 3: Competitive Pricing
* * *

This model builds upon Model 2 by considering the prices of nearby competing parking lots. It adjusts a lot's price based on the average price of its competitors within a certain radius.

### Calculate Distances Between Parking Lots

In [13]:
# Get unique parking lots with their locations
lots_df = df_model2[['SystemCodeNumber', 'Latitude', 'Longitude']].drop_duplicates().reset_index(drop=True)

# Haversine formula to compute distance (in km)
def haversine(lat1, lon1, lat2, lon2):
    R = 6371  # Earth radius in km
    phi1, phi2 = np.radians(lat1), np.radians(lat2)
    delta_phi = np.radians(lat2 - lat1)
    delta_lambda = np.radians(lon2 - lon1)

    a = np.sin(delta_phi/2)**2 + np.cos(phi1) * np.cos(phi2) * np.sin(delta_lambda/2)**2
    return R * 2 * np.arcsin(np.sqrt(a))

# Build distance matrix between all pairs of lots
distance_matrix = pd.DataFrame(index=lots_df['SystemCodeNumber'], columns=lots_df['SystemCodeNumber'], dtype=float)

for i, row_i in lots_df.iterrows():
    for j, row_j in lots_df.iterrows():
        if i == j:
            distance_matrix.loc[row_i['SystemCodeNumber'], row_j['SystemCodeNumber']] = 0.0
        else:
            dist = haversine(row_i['Latitude'], row_i['Longitude'], row_j['Latitude'], row_j['Longitude'])
            distance_matrix.loc[row_i['SystemCodeNumber'], row_j['SystemCodeNumber']] = dist

display("Sample distance matrix (in km):", distance_matrix.round(3).iloc[:5, :5])

'Sample distance matrix (in km):'

SystemCodeNumber  BHMBCCMKT01  BHMBCCTHL01  BHMEURBRD01  BHMMBMMBX01  \
SystemCodeNumber                                                       
BHMBCCMKT01             0.000        0.006        0.599     1561.110   
BHMBCCTHL01             0.006        0.000        0.601     1561.111   
BHMEURBRD01             0.599        0.601        0.000     1561.611   
BHMMBMMBX01          1561.110     1561.111     1561.611        0.000   
BHMNCPHST01             0.721        0.720        1.313     1560.438   

SystemCodeNumber  BHMNCPHST01  
SystemCodeNumber               
BHMBCCMKT01             0.721  
BHMBCCTHL01             0.720  
BHMEURBRD01             1.313  
BHMMBMMBX01          1560.438  
BHMNCPHST01             0.000

### Apply Competitive Pricing Logic

In [14]:
df_model3 = df_model2.copy()

# Ensure data is sorted by lot and time for correct processing
df_model3 = df_model3.sort_values(by=['SystemCodeNumber', 'Timestamp'])

# Round timestamps to buckets for finding competitors at roughly the same time
df_model3['TimeBucket'] = df_model3['Timestamp'].dt.floor('30min')

# Set radius to define "nearby" (in km) for competition
NEARBY_RADIUS_KM = 1.0

# Initialize Model 3 price with Model 2 baseline prices
df_model3['Price_Model3'] = df_model3['Price_Model2']

# Loop through each row and adjust price based on nearby competitors
for idx, row in df_model3.iterrows():
    current_lot = row['SystemCodeNumber']
    time_bucket = row['TimeBucket']
    current_price = row['Price_Model2']
    occupancy_ratio = row['Occupancy'] / row['Capacity']

    # Find nearby lot names within the radius (excluding the current lot)
    nearby_lots = distance_matrix.loc[current_lot]
    nearby_lots = nearby_lots[(nearby_lots > 0) & (nearby_lots <= NEARBY_RADIUS_KM)].index.tolist()

    if not nearby_lots:
        continue  # No nearby competition to consider

    # Get nearby competitors' Model 2 prices in the same time bucket
    mask = (df_model3['SystemCodeNumber'].isin(nearby_lots)) & \
           (df_model3['TimeBucket'] == time_bucket)

    nearby_prices = df_model3.loc[mask, 'Price_Model2']

    if nearby_prices.empty:
        continue  # No competitors updated at the same time bucket

    # Calculate the average price of nearby competitors
    avg_competitor_price = nearby_prices.mean()

    # Apply competitive pricing rules
    adjusted_price = current_price

    # Rule: If our lot's Model 2 price is higher than competitors' average price
    # AND the lot is highly occupied (>90%), slightly reduce our price to remain competitive.
    if current_price > avg_competitor_price and occupancy_ratio > 0.9:
        adjusted_price = current_price * 0.95  # Apply a small discount

    # Rule: If our lot's Model 2 price is lower than competitors' average price,
    # slightly increase our price to capitalize on less expensive positioning.
    elif current_price < avg_competitor_price:
        adjusted_price = current_price * 1.05 # Apply a small premium

    # Optional: Clip the adjusted price to stay within a reasonable range
    df_model3.at[idx, 'Price_Model3'] = np.clip(adjusted_price, 5, 20.5) # Slightly increased upper limit for potential small increases

### Preview Model 3 Prices

In [15]:
df_model3[['SystemCodeNumber', 'TimeBucket', 'Occupancy', 'Price_Model2', 'Price_Model3']].head(10)

SystemCodeNumber          TimeBucket  Occupancy  Price_Model2  Price_Model3
0      BHMBCCMKT01 2016-10-04 07:30:00         61     11.365295     11.365295
1      BHMBCCMKT01 2016-10-04 08:00:00         64     11.368170     11.368170
2      BHMBCCMKT01 2016-10-04 08:30:00         80     12.305159     12.305159
3      BHMBCCMKT01 2016-10-04 09:30:00        107     12.331035     12.331035
4      BHMBCCMKT01 2016-10-04 09:30:00        150     12.353813     12.353813
5      BHMBCCMKT01 2016-10-04 10:00:00        177     13.319777     13.319777
6      BHMBCCMKT01 2016-10-04 10:30:00        219     15.774765     15.774765
7      BHMBCCMKT01 2016-10-04 11:00:00        247     15.045843     15.045843
8      BHMBCCMKT01 2016-10-04 11:30:00        259     15.031537     15.031537
9      BHMBCCMKT01 2016-10-04 12:00:00        266     17.626252     17.626252

* * *
### Consolidate and Compare Prices
* * *

Combine the prices from all three models into a single DataFrame for easier comparison and analysis.

In [16]:
# Select and order relevant columns from the final DataFrame (df_model3 contains all calculated prices)
comparison_df = df_model3[[
    'SystemCodeNumber', 'Timestamp', 'Occupancy',
    'Price_Model1', 'Price_Model2', 'Price_Model3'
]].copy()

# Round prices for clarity
comparison_df[['Price_Model1', 'Price_Model2', 'Price_Model3']] = comparison_df[
    ['Price_Model1', 'Price_Model2', 'Price_Model3']
].round(2)

# Display the top rows of the comparison DataFrame
display(comparison_df.head())

SystemCodeNumber           Timestamp  Occupancy  Price_Model1  Price_Model2  \
0      BHMBCCMKT01 2016-10-04 07:59:00         61         10.53         11.37   
1      BHMBCCMKT01 2016-10-04 08:25:00         64         10.55         11.37   
2      BHMBCCMKT01 2016-10-04 08:59:00         80         10.69         12.31   
3      BHMBCCMKT01 2016-10-04 09:32:00        107         10.93         12.33   
4      BHMBCCMKT01 2016-10-04 09:59:00        150         11.30         12.35   

   Price_Model3  
0         11.37  
1         11.37  
2         12.31  
3         12.33  
4         12.35

### Summary Statistics of Prices
* * *

Calculate and display summary statistics (mean, std, min, max, quartiles) for the prices generated by each model.

In [17]:
summary_stats = comparison_df[['Price_Model1', 'Price_Model2', 'Price_Model3']].describe().round(2)
print("📊 Summary Statistics (Price in $):")
display(summary_stats)

📊 Summary Statistics (Price in $):


Price_Model1  Price_Model2  Price_Model3
count      18368.00      18368.00      18368.00
mean          12.55         13.38         13.66
std            1.23          2.11          2.08
min           10.02         10.00         10.00
25%           11.54         11.64         11.91
50%           12.48         12.81         13.13
75%           13.51         14.88         15.13
max           15.21         20.00         20.18

### Analysis of Price Differences
* * *

Calculate the differences between the prices generated by the models to understand how they vary.

In [18]:
# Calculate differences between model prices
comparison_df['Diff_2_vs_1'] = comparison_df['Price_Model2'] - comparison_df['Price_Model1']
comparison_df['Diff_3_vs_2'] = comparison_df['Price_Model3'] - comparison_df['Price_Model2']
comparison_df['Diff_3_vs_1'] = comparison_df['Price_Model3'] - comparison_df['Price_Model1']

# Summary statistics for the price differences
diff_summary = comparison_df[['Diff_2_vs_1', 'Diff_3_vs_2', 'Diff_3_vs_1']].describe().round(4)
print("📉 Difference Summary (in dollars):")
display(diff_summary)

📉 Difference Summary (in dollars):


Diff_2_vs_1  Diff_3_vs_2  Diff_3_vs_1
count   18368.0000   18368.0000   18368.0000
mean        0.8349       0.2796       1.1144
std         2.0765       0.3812       2.1049
min        -4.0800      -1.0000      -4.0700
25%        -0.7300       0.0000      -0.4300
50%         0.4400       0.0000       0.7500
75%         2.1200       0.6200       2.4100
max         8.7500       0.9600       8.8700

* * *
### Visualize Price Comparisons
* * *

Generate plots to visualize how the prices from Model 2 and Model 3 compare over time for each parking lot. Model 1 is excluded from these plots for better readability, as Model 2 and 3 are built upon more features.

In [19]:
# Sort data by lot and timestamp for plotting
df_model3 = df_model3.sort_values(by=["SystemCodeNumber", "Timestamp"])

# Get list of all unique parking lots
parking_lots = df_model3['SystemCodeNumber'].unique()

# Prepare a list to hold plots for each parking lot
plots = []

# Generate and add a plot for each parking lot
for lot in parking_lots:
    lot_df = df_model3[df_model3['SystemCodeNumber'] == lot]

    # Use ColumnDataSource for better performance with Bokeh
    source = ColumnDataSource(lot_df)

    # Create a new figure for the current parking lot
    p = figure(
        title=f"Price Comparison for Lot: {lot}",
        x_axis_label='Time',
        y_axis_label='Price ($)',
        x_axis_type='datetime',
        width=800,
        height=300,
        tools="pan,wheel_zoom,box_zoom,reset,save" # Add interactive tools
    )

    # Add lines for Model 2 and Model 3 prices
    l2 = p.line(x='Timestamp', y='Price_Model2', source=source, color='blue', line_width=2, legend_label='Model 2')
    l3 = p.line(x='Timestamp', y='Price_Model3', source=source, color='red', line_width=2, legend_label='Model 3')

    # Configure legend
    p.legend.location = "top_left"
    p.legend.click_policy = "hide" # Allows toggling lines by clicking legend

    # Add the plot to the list
    plots.append(p)

# Show all plots vertically stacked
show(column(*plots))

### Correlation Analysis of Features and Prices

In [20]:
# Select features used in Model 2 and the calculated prices
feature_corr = df_model3[[
    'OccupancyRatio',
    'QueueLength',
    'TrafficLevel',
    'IsSpecialDay',
    'VehicleTypeWeight',
    'Price_Model1',
    'Price_Model2',
    'Price_Model3'
]]

# Calculate the correlation matrix
correlation_matrix = feature_corr.corr().round(2)

print("📈 Correlation Matrix:")
display(correlation_matrix)

📈 Correlation Matrix:


OccupancyRatio  QueueLength  TrafficLevel  IsSpecialDay  \
OccupancyRatio               1.00         0.26          0.26         -0.24   
QueueLength                  0.26         1.00          0.87          0.18   
TrafficLevel                 0.26         0.87          1.00         -0.00   
IsSpecialDay                -0.24         0.18         -0.00          1.00   
VehicleTypeWeight           -0.00        -0.01         -0.02          0.01   
Price_Model1                 1.00         0.26          0.26         -0.24   
Price_Model2                 0.32         0.96          0.88          0.12   
Price_Model3                 0.27         0.96          0.87          0.13   

                   VehicleTypeWeight  Price_Model1  Price_Model2  Price_Model3  
OccupancyRatio                 -0.00          1.00          0.32          0.27  
QueueLength                    -0.01          0.26          0.96          0.96  
TrafficLevel                   -0.02          0.26          0.88          0.87  
IsSpecialDay                    0.01         -0.24          0.12          0.13  
VehicleTypeWeight               1.00         -0.00         -0.01         -0.02  
Price_Model1                   -0.00          1.00          0.32          0.27  
Price_Model2                   -0.01          0.32          1.00          0.98  
Price_Model3                   -0.02          0.27          0.98          1.00

### Visualize Price Distributions
* * *

Generate plots to visualize the distribution of prices for each model.

In [21]:
from bokeh.transform import factor_cmap
from bokeh.models import FactorRange
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource
from bokeh.palettes import Category10

# Prepare data for plotting price distributions
# We'll use the comparison_df which already has prices from all models
price_distribution_df = comparison_df[['Price_Model1', 'Price_Model2', 'Price_Model3']].melt(var_name='Model', value_name='Price')

# Create a list of models for the x-axis
models = ['Price_Model1', 'Price_Model2', 'Price_Model3']

# Create a ColumnDataSource from the melted DataFrame
source = ColumnDataSource(price_distribution_df)

# Create a figure for the price distribution
p_dist = figure(
    x_range=FactorRange(*models),
    title="Price Distribution by Model",
    x_axis_label="Pricing Model",
    y_axis_label="Price ($)",
    height=300,
    tools="pan,wheel_zoom,box_zoom,reset,save"
)

# Calculate quartiles, IQR, and outliers for each model
# This data is needed for drawing box plots
# Using pandas groupby and quantile for calculations
grouped = price_distribution_df.groupby('Model')['Price']
q1 = grouped.quantile(q=0.25)
q2 = grouped.quantile(q=0.5) # median
q3 = grouped.quantile(q=0.75)
iqr = q3 - q1
upper_outliers = q3 + 1.5 * iqr
lower_outliers = q1 - 1.5 * iqr

# Create a new dataframe for box plot data
box_plot_data = pd.DataFrame({
    'Model': models,
    'q1': q1.loc[models].values,
    'q2': q2.loc[models].values,
    'q3': q3.loc[models].values,
    'iqr': iqr.loc[models].values,
    'upper': q3.loc[models].values + 1.5*iqr.loc[models].values,
    'lower': q1.loc[models].values - 1.5*iqr.loc[models].values
})

# Draw the box and whiskers
# Whiskers
p_dist.segment(x0='Model', y0='upper', x1='Model', y1='q3', source=ColumnDataSource(box_plot_data), line_color="black")
p_dist.segment(x0='Model', y0='lower', x1='Model', y1='q1', source=ColumnDataSource(box_plot_data), line_color="black")

# Boxes
p_dist.vbar(x='Model', top='q3', bottom='q2', width=0.7, source=ColumnDataSource(box_plot_data), line_color="black", fill_color=factor_cmap('Model', palette=Category10[3], factors=models))
p_dist.vbar(x='Model', top='q2', bottom='q1', width=0.7, source=ColumnDataSource(box_plot_data), line_color="black", fill_color=factor_cmap('Model', palette=Category10[3], factors=models))

# Outliers (optional) - need to filter outliers from the original data
def identify_outliers(group):
    q1 = group.quantile(0.25)
    q3 = group.quantile(0.75)
    iqr = q3 - q1
    upper = q3 + 1.5 * iqr
    lower = q1 - 1.5 * iqr
    return group[(group > upper) | (group < lower)]

outliers = price_distribution_df.groupby('Model')['Price'].apply(identify_outliers).reset_index()
if not outliers.empty:
    p_dist.circle(x='Model', y='Price', source=ColumnDataSource(outliers), size=6, color="black", alpha=0.6)


# Customize appearance
p_dist.xgrid.grid_line_color = None
p_dist.y_range.start = 0

# Show the plot
show(p_dist)

In [22]:
!pip install pathway bokeh --quiet

In [23]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime
from datetime import datetime
import pathway as pw
import bokeh.plotting
import panel as pn

In [24]:
df = pd.read_csv('dataset.csv')
df

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy  \
0          0      BHMBCCMKT01       577  26.144536  91.736172         61   
1          1      BHMBCCMKT01       577  26.144536  91.736172         64   
2          2      BHMBCCMKT01       577  26.144536  91.736172         80   
3          3      BHMBCCMKT01       577  26.144536  91.736172        107   
4          4      BHMBCCMKT01       577  26.144536  91.736172        150   
...      ...              ...       ...        ...        ...        ...   
18363  18363         Shopping      1920  26.150504  91.733531       1517   
18364  18364         Shopping      1920  26.150504  91.733531       1487   
18365  18365         Shopping      1920  26.150504  91.733531       1432   
18366  18366         Shopping      1920  26.150504  91.733531       1321   
18367  18367         Shopping      1920  26.150504  91.733531       1180   

      VehicleType TrafficConditionNearby  QueueLength  IsSpecialDay  \
0             car                    low            1             0   
1             car                    low            1             0   
2             car                    low            2             0   
3             car                    low            2             0   
4            bike                    low            2             0   
...           ...                    ...          ...           ...   
18363       truck                average            6             0   
18364         car                    low            3             0   
18365       cycle                    low            3             0   
18366         car                    low            2             0   
18367         car                    low            2             0   

      LastUpdatedDate LastUpdatedTime  
0          04-10-2016        07:59:00  
1          04-10-2016        08:25:00  
2          04-10-2016        08:59:00  
3          04-10-2016        09:32:00  
4          04-10-2016        09:59:00  
...               ...             ...  
18363      19-12-2016        14:30:00  
18364      19-12-2016        15:03:00  
18365      19-12-2016        15:29:00  
18366      19-12-2016        16:03:00  
18367      19-12-2016        16:30:00  

[18368 rows x 12 columns]

In [25]:
df['Timestamp'] = pd.to_datetime(df['LastUpdatedDate'] + ' ' + df['LastUpdatedTime'],
                                  format='%d-%m-%Y %H:%M:%S')

df = df.sort_values('Timestamp').reset_index(drop=True)

In [26]:
df[["Timestamp", "Occupancy", "Capacity"]].to_csv("parking_stream.csv", index=False)

In [27]:
class ParkingSchema(pw.Schema):
    Timestamp: str   # Timestamp of the observation (should ideally be in ISO format)
    Occupancy: int   # Number of occupied parking spots
    Capacity: int    # Total parking capacity at the location

In [28]:
data = pw.demo.replay_csv("parking_stream.csv", schema=ParkingSchema, input_rate=1000)

In [29]:
fmt = "%Y-%m-%d %H:%M:%S"

# Add new columns to the data stream:
# - 't' contains the parsed full datetime
# - 'day' extracts the date part and resets the time to midnight (useful for day-level aggregations)
data_with_time = data.with_columns(
    t = data.Timestamp.dt.strptime(fmt),
    day = data.Timestamp.dt.strptime(fmt).dt.strftime("%Y-%m-%dT00:00:00")
)


In [30]:
import datetime

delta_window = (
    data_with_time.windowby(
        pw.this.t,  # Event time column to use for windowing (parsed datetime)
        instance=pw.this.day,  # Logical partitioning key: one instance per calendar day
        window=pw.temporal.tumbling(datetime.timedelta(days=1)),  # Fixed-size daily window
        behavior=pw.temporal.exactly_once_behavior()  # Guarantees exactly-once processing semantics
    )
    .reduce(
        t=pw.this._pw_window_end,                        # Assign the end timestamp of each window
        occ_max=pw.reducers.max(pw.this.Occupancy),      # Highest occupancy observed in the window
        occ_min=pw.reducers.min(pw.this.Occupancy),      # Lowest occupancy observed in the window
        cap=pw.reducers.max(pw.this.Capacity),           # Maximum capacity observed (typically constant per spot)
    )
    .with_columns(
        # Compute the price using a simple dynamic pricing formula:
        #
        # Pricing Formula:
        #     price = base_price + demand_fluctuation
        #     where:
        #         base_price = 10 (fixed minimum price)
        #         demand_fluctuation = (occ_max - occ_min) / cap
        #
        # Intuition:
        # - The greater the difference between peak and low occupancy in a day,
        #   the more volatile the demand is, indicating potential scarcity.
        # - Dividing by capacity normalizes the fluctuation (to stay in [0,1] range).
        # - This fluctuation is added to the base price of 10 to set the final price.
        # - Example: If occ_max = 90, occ_min = 30, cap = 100
        #            => price = 10 + (90 - 30)/100 = 10 + 0.6 = 10.6

        price=10 + (pw.this.occ_max - pw.this.occ_min) / pw.this.cap
    )
)

In [31]:
# Activate the Panel extension to enable interactive visualizations
pn.extension()

# Define a custom Bokeh plotting function that takes a data source (from Pathway) and returns a figure
def price_plotter(source):
    # Create a Bokeh figure with datetime x-axis
    fig = bokeh.plotting.figure(
        height=400,
        width=800,
        title="Pathway: Daily Parking Price",
        x_axis_type="datetime",  # Ensure time-based data is properly formatted on the x-axis
    )
    # Plot a line graph showing how the price evolves over time
    fig.line("t", "price", source=source, line_width=2, color="navy")

    # Overlay red circles at each data point for better visibility
    fig.circle("t", "price", source=source, size=6, color="red")

    return fig

# Use Pathway's built-in .plot() method to bind the data stream (delta_window) to the Bokeh plot
# - 'price_plotter' is the rendering function
# - 'sorting_col="t"' ensures the data is plotted in time order
viz = delta_window.plot(price_plotter, sorting_col="t")

# Create a Panel layout and make it servable as a web app
# This line enables the interactive plot to be displayed when the app is served
pn.Column(viz).servable()

Column
    [0] Column
        [0] Row
            [0] Markdown(str)
            [1] TooltipIcon(value='Table depends o...)
        [1] Bokeh(figure)

In [32]:
%%capture --no-display
pw.run()

Output()

* * *
### Simulation: Model 1 (Simple Occupancy-Based Pricing)
* * *

Simulate Model 1 pricing based on occupancy ratio.

In [33]:
# Model 1: Simple Occupancy-Based Pricing
# Formula: Price = Base Price + Alpha * (Occupancy / Capacity)

# Define parameters for Model 1
BASE_PRICE_SIM_M1 = 10.0  # Base price in dollars
ALPHA_SIM_M1 = 5.0       # Sensitivity of price to occupancy

# Ensure capacity is available for each lot
if 'Capacity' not in df.columns:
    # Get capacity for each lot (assuming capacity is constant per SystemCodeNumber)
    capacity_dict_sim = df.groupby('SystemCodeNumber')['Capacity'].first().to_dict()
    df['Capacity'] = df['SystemCodeNumber'].map(capacity_dict_sim)

# Calculate Model 1 price
df['OccupancyRatio_sim_M1'] = df['Occupancy'] / df['Capacity']
df['Price_Model1_sim'] = BASE_PRICE_SIM_M1 + ALPHA_SIM_M1 * df['OccupancyRatio_sim_M1']

print("✅ Model 1 Simulation Complete. Preview of results:")
display(df[['SystemCodeNumber', 'LastUpdatedDate', 'LastUpdatedTime', 'Occupancy', 'Capacity', 'Price_Model1_sim']].head(15))

✅ Model 1 Simulation Complete. Preview of results:


SystemCodeNumber LastUpdatedDate LastUpdatedTime  Occupancy  Capacity  \
0        BHMBCCMKT01      04-10-2016        07:59:00         61       577   
1        BHMNCPHST01      04-10-2016        07:59:00        237      1200   
2        BHMMBMMBX01      04-10-2016        07:59:00        264       687   
3        BHMNCPNST01      04-10-2016        07:59:00        249       485   
4           Shopping      04-10-2016        07:59:00        614      1920   
5        BHMEURBRD01      04-10-2016        07:59:00        117       470   
6       Broad Street      04-10-2016        07:59:00        178       690   
7      Others-CCCPS8      04-10-2016        07:59:00        445      1322   
8   Others-CCCPS105a      04-10-2016        07:59:00        709      2009   
9   Others-CCCPS119a      04-10-2016        07:59:00        195      2803   
10       BHMBCCTHL01      04-10-2016        07:59:00        120       387   
11  Others-CCCPS135a      04-10-2016        07:59:00       1081      3883   
12   Others-CCCPS202      04-10-2016        07:59:00        547      2937   
13    Others-CCCPS98      04-10-2016        07:59:00        588      3103   
14     Others-CCCPS8      04-10-2016        08:25:00        478      1322   

    Price_Model1_sim  
0          10.528596  
1          10.987500  
2          11.921397  
3          12.567010  
4          11.598958  
5          11.244681  
6          11.289855  
7          11.683056  
8          11.764559  
9          10.347842  
10         11.550388  
11         11.391965  
12         10.931222  
13         10.947470  
14         11.807867

* * *
### Simulation: Model 2 (Feature-Rich Demand Model)
* * *

Simulate Model 2 pricing incorporating multiple features to estimate demand.

In [34]:
# Model 2: Feature-Rich Demand Model
# Incorporates Occupancy Ratio, Queue Length, Traffic Condition, Is Special Day, Vehicle Type

df_sim_model2 = df.copy()

# Combine date and time into Timestamp if not already done
if 'Timestamp' not in df_sim_model2.columns:
    df_sim_model2['Timestamp'] = pd.to_datetime(
        df_sim_model2['LastUpdatedDate'] + ' ' + df_sim_model2['LastUpdatedTime'],
        dayfirst=True
    )

# Map categorical features to numerical values if not already done
if 'TrafficLevel' not in df_sim_model2.columns:
    traffic_map_sim = {'low': 0, 'average': 1, 'high': 2}
    df_sim_model2['TrafficLevel'] = df_sim_model2['TrafficConditionNearby'].map(traffic_map_sim)

if 'VehicleTypeWeight' not in df_sim_model2.columns:
    vehicle_weights_sim = {'car': 1.0, 'bike': 0.5, 'truck': 1.5, 'cycle': 0.3}
    df_sim_model2['VehicleTypeWeight'] = df_sim_model2['VehicleType'].map(vehicle_weights_sim)

# Ensure capacity and occupancy ratio are available
if 'Capacity' not in df_sim_model2.columns:
    capacity_dict_sim = df_sim_model2.groupby('SystemCodeNumber')['Capacity'].first().to_dict()
    df_sim_model2['Capacity'] = df_sim_model2['SystemCodeNumber'].map(capacity_dict_sim)

if 'OccupancyRatio' not in df_sim_model2.columns:
     df_sim_model2['OccupancyRatio'] = df_sim_model2['Occupancy'] / df_sim_model2['Capacity']


# Define weights for each factor (tuned based on analysis)
alpha_sim_m2 = 1.5    # OccupancyRatio
beta_sim_m2 = 2.5     # QueueLength
gamma_sim_m2 = 0.5    # TrafficLevel (penalty)
delta_sim_m2 = -1.0   # IsSpecialDay (slight negative impact on demand)
epsilon_sim_m2 = 0.1  # VehicleTypeWeight (optional, very weak)

# Compute Raw Demand
df_sim_model2['RawDemand_sim_M2'] = (
    alpha_sim_m2 * df_sim_model2['OccupancyRatio']
  + beta_sim_m2 * df_sim_model2['QueueLength']
  - gamma_sim_m2 * df_sim_model2['TrafficLevel']
  + delta_sim_m2 * df_sim_model2['IsSpecialDay']
  + epsilon_sim_m2 * df_sim_model2['VehicleTypeWeight']
)

# Normalize Demand per Parking Lot
df_sim_model2['NormalizedDemand_sim_M2'] = df_sim_model2.groupby('SystemCodeNumber')['RawDemand_sim_M2'].transform(
    lambda x: (x - x.min()) / (x.max() - x.min() + 1e-6)
)

# Calculate Model 2 Price
BASE_PRICE_SIM_M2 = 10
LAMBDA_SIM_M2 = 1.0  # how much normalized demand affects price

df_sim_model2['Price_Model2_sim'] = BASE_PRICE_SIM_M2 * (1 + LAMBDA_SIM_M2 * df_sim_model2['NormalizedDemand_sim_M2'])

# Optional: Clip price to reasonable bounds
df_sim_model2['Price_Model2_sim'] = df_sim_model2['Price_Model2_sim'].clip(lower=5, upper=20)

print("✅ Model 2 Simulation Complete. Preview of results:")
display(df_sim_model2[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'QueueLength', 'TrafficLevel', 'IsSpecialDay', 'NormalizedDemand_sim_M2', 'Price_Model2_sim']].head(10))

✅ Model 2 Simulation Complete. Preview of results:


SystemCodeNumber           Timestamp  Occupancy  QueueLength  TrafficLevel  \
0       BHMBCCMKT01 2016-10-04 07:59:00         61            1             0   
1       BHMNCPHST01 2016-10-04 07:59:00        237            2             0   
2       BHMMBMMBX01 2016-10-04 07:59:00        264            2             0   
3       BHMNCPNST01 2016-10-04 07:59:00        249            2             0   
4          Shopping 2016-10-04 07:59:00        614            2             0   
5       BHMEURBRD01 2016-10-04 07:59:00        117            2             0   
6      Broad Street 2016-10-04 07:59:00        178            2             0   
7     Others-CCCPS8 2016-10-04 07:59:00        445            3             1   
8  Others-CCCPS105a 2016-10-04 07:59:00        709            2             0   
9  Others-CCCPS119a 2016-10-04 07:59:00        195            1             0   

   IsSpecialDay  NormalizedDemand_sim_M2  Price_Model2_sim  
0             0                 0.136529         11.365295  
1             0                 0.131774         11.317738  
2             0                 0.095224         10.952241  
3             0                 0.127111         11.271109  
4             0                 0.092962         10.929620  
5             0                 0.194554         11.945539  
6             0                 0.136044         11.360438  
7             0                 0.162519         11.625189  
8             0                 0.084415         10.844147  
9             0                 0.037038         10.370377

* * *
### Simulation: Model 3 (Competitive Pricing)
* * *

Simulate Model 3 pricing, incorporating competitive pricing based on nearby lots.

In [35]:
# Model 3: Competitive Pricing
# Builds upon Model 2 and considers the prices of nearby competing parking lots.

df_sim_model3 = df.copy()

# Ensure Timestamp, Capacity, OccupancyRatio, TrafficLevel, VehicleTypeWeight, RawDemand, NormalizedDemand, and Price_Model2 are available (from previous steps or recalculate)
if 'Timestamp' not in df_sim_model3.columns:
    df_sim_model3['Timestamp'] = pd.to_datetime(
        df_sim_model3['LastUpdatedDate'] + ' ' + df_sim_model3['LastUpdatedTime'],
        dayfirst=True
    )

if 'Capacity' not in df_sim_model3.columns:
    capacity_dict_sim = df_sim_model3.groupby('SystemCodeNumber')['Capacity'].first().to_dict()
    df_sim_model3['Capacity'] = df_sim_model3['SystemCodeNumber'].map(capacity_dict_sim)

if 'OccupancyRatio' not in df_sim_model3.columns:
     df_sim_model3['OccupancyRatio'] = df_sim_model3['Occupancy'] / df_sim_model3['Capacity']

if 'TrafficLevel' not in df_sim_model3.columns:
    traffic_map_sim = {'low': 0, 'average': 1, 'high': 2}
    df_sim_model3['TrafficLevel'] = df_sim_model3['TrafficConditionNearby'].map(traffic_map_sim)

if 'VehicleTypeWeight' not in df_sim_model3.columns:
    vehicle_weights_sim = {'car': 1.0, 'bike': 0.5, 'truck': 1.5, 'cycle': 0.3}
    df_sim_model3['VehicleTypeWeight'] = df_sim_model3['VehicleType'].map(vehicle_weights_sim)

# Recalculate RawDemand and NormalizedDemand if necessary
if 'RawDemand' not in df_sim_model3.columns or 'NormalizedDemand' not in df_sim_model3.columns:
    alpha_sim_m2 = 1.5
    beta_sim_m2 = 2.5
    gamma_sim_m2 = 0.5
    delta_sim_m2 = -1.0
    epsilon_sim_m2 = 0.1

    df_sim_model3['RawDemand'] = (
        alpha_sim_m2 * df_sim_model3['OccupancyRatio']
      + beta_sim_m2 * df_sim_model3['QueueLength']
      - gamma_sim_m2 * df_sim_model3['TrafficLevel']
      + delta_sim_m2 * df_sim_model3['IsSpecialDay']
      + epsilon_sim_m2 * df_sim_model3['VehicleTypeWeight']
    )

    df_sim_model3['NormalizedDemand'] = df_sim_model3.groupby('SystemCodeNumber')['RawDemand'].transform(
        lambda x: (x - x.min()) / (x.max() - x.min() + 1e-6)
    )

# Recalculate Price_Model2 if necessary
if 'Price_Model2' not in df_sim_model3.columns:
    BASE_PRICE_SIM_M2 = 10
    LAMBDA_SIM_M2 = 1.0
    df_sim_model3['Price_Model2'] = BASE_PRICE_SIM_M2 * (1 + LAMBDA_SIM_M2 * df_sim_model3['NormalizedDemand'])
    df_sim_model3['Price_Model2'] = df_sim_model3['Price_Model2'].clip(lower=5, upper=20)


# Calculate distances between parking lots if not already available
if 'distance_matrix' not in globals():
    # Get unique parking lots with their locations
    lots_df_sim = df_sim_model3[['SystemCodeNumber', 'Latitude', 'Longitude']].drop_duplicates().reset_index(drop=True)

    # Haversine formula to compute distance (in km)
    def haversine_sim(lat1, lon1, lat2, lon2):
        R = 6371  # Earth radius in km
        phi1, phi2 = np.radians(lat1), np.radians(lat2)
        delta_phi = np.radians(lat2 - lat1)
        delta_lambda = np.radians(lon2 - lon1)

        a = np.sin(delta_phi/2)**2 + np.cos(phi1) * np.cos(phi2) * np.sin(delta_lambda/2)**2
        return R * 2 * np.arcsin(np.sqrt(a))

    # Build distance matrix between all pairs of lots
    distance_matrix = pd.DataFrame(index=lots_df_sim['SystemCodeNumber'], columns=lots_df_sim['SystemCodeNumber'], dtype=float)

    for i, row_i in lots_df_sim.iterrows():
        for j, row_j in lots_df_sim.iterrows():
            if i == j:
                distance_matrix.loc[row_i['SystemCodeNumber'], row_j['SystemCodeNumber']] = 0.0
            else:
                dist = haversine_sim(row_i['Latitude'], row_i['Longitude'], row_j['Latitude'], row_j['Longitude'])
                distance_matrix.loc[row_i['SystemCodeNumber'], row_j['SystemCodeNumber']] = dist


# Ensure data is sorted by lot and time for correct processing
df_sim_model3 = df_sim_model3.sort_values(by=['SystemCodeNumber', 'Timestamp'])

# Round timestamps to buckets for finding competitors at roughly the same time
df_sim_model3['TimeBucket_sim_M3'] = df_sim_model3['Timestamp'].dt.floor('30min')

# Set radius to define "nearby" (in km) for competition
NEARBY_RADIUS_KM_SIM_M3 = 1.0

# Initialize Model 3 price with Model 2 baseline prices
df_sim_model3['Price_Model3_sim'] = df_sim_model3['Price_Model2']

# Loop through each row and adjust price based on nearby competitors
for idx, row in df_sim_model3.iterrows():
    current_lot = row['SystemCodeNumber']
    time_bucket = row['TimeBucket_sim_M3']
    current_price = row['Price_Model2']
    occupancy_ratio = row['Occupancy'] / row['Capacity']

    # Find nearby lot names within the radius (excluding the current lot)
    if current_lot in distance_matrix.index:
        nearby_lots = distance_matrix.loc[current_lot]
        nearby_lots = nearby_lots[(nearby_lots > 0) & (nearby_lots <= NEARBY_RADIUS_KM_SIM_M3)].index.tolist()
    else:
        nearby_lots = []


    if not nearby_lots:
        continue  # No nearby competition to consider

    # Get nearby competitors' Model 2 prices in the same time bucket
    mask = (df_sim_model3['SystemCodeNumber'].isin(nearby_lots)) & \
           (df_sim_model3['TimeBucket_sim_M3'] == time_bucket)

    nearby_prices = df_sim_model3.loc[mask, 'Price_Model2']

    if nearby_prices.empty:
        continue  # No competitors updated at the same time bucket

    # Calculate the average price of nearby competitors
    avg_competitor_price = nearby_prices.mean()

    # Apply competitive pricing rules
    adjusted_price = current_price

    # Rule: If our lot's Model 2 price is higher than competitors' average price
    # AND the lot is highly occupied (>90%), slightly reduce our price to remain competitive.
    if current_price > avg_competitor_price and occupancy_ratio > 0.9:
        adjusted_price = current_price * 0.95  # Apply a small discount

    # Rule: If our lot's Model 2 price is lower than competitors' average price,
    # slightly increase our price to capitalize on less expensive positioning.
    elif current_price < avg_competitor_price:
        adjusted_price = current_price * 1.05 # Apply a small premium

    # Optional: Clip the adjusted price to stay within a reasonable range
    df_sim_model3.at[idx, 'Price_Model3_sim'] = np.clip(adjusted_price, 5, 20.5) # Slightly increased upper limit for potential small increases

print("✅ Model 3 Simulation Complete. Preview of results:")
display(df_sim_model3[['SystemCodeNumber', 'TimeBucket_sim_M3', 'Occupancy', 'Price_Model2', 'Price_Model3_sim']].head(10))

✅ Model 3 Simulation Complete. Preview of results:


SystemCodeNumber   TimeBucket_sim_M3  Occupancy  Price_Model2  \
0        BHMBCCMKT01 2016-10-04 07:30:00         61     11.365295   
27       BHMBCCMKT01 2016-10-04 08:00:00         64     11.368170   
37       BHMBCCMKT01 2016-10-04 08:30:00         80     12.305159   
50       BHMBCCMKT01 2016-10-04 09:30:00        107     12.331035   
67       BHMBCCMKT01 2016-10-04 09:30:00        150     12.353813   
74       BHMBCCMKT01 2016-10-04 10:00:00        177     13.319777   
93       BHMBCCMKT01 2016-10-04 10:30:00        219     15.774765   
100      BHMBCCMKT01 2016-10-04 11:00:00        247     15.045843   
114      BHMBCCMKT01 2016-10-04 11:30:00        259     15.031537   
128      BHMBCCMKT01 2016-10-04 12:00:00        266     17.626252   

     Price_Model3_sim  
0           11.365295  
27          11.368170  
37          12.305159  
50          12.331035  
67          12.353813  
74          13.319777  
93          15.774765  
100         15.045843  
114         15.031537  
128         17.626252

* * *
### Visualize Price Comparisons (Simulated Data)
* * *

Generate plots to visualize how the simulated prices from Model 1, Model 2, and Model 3 compare over time for each parking lot.

In [39]:
# Ensure the necessary dataframes from the simulations are available
# Assuming df_sim_model1, df_sim_model2, and df_sim_model3 exist after running the simulation cells

# Merge the simulated prices into a single DataFrame for easier plotting
comparison_sim_df = df[['SystemCodeNumber', 'Timestamp', 'Price_Model1_sim']].copy()
comparison_sim_df = comparison_sim_df.merge(
    df_sim_model2[['SystemCodeNumber', 'Timestamp', 'Price_Model2_sim']],
    on=['SystemCodeNumber', 'Timestamp'],
    how='left'
)
comparison_sim_df = comparison_sim_df.merge(
    df_sim_model3[['SystemCodeNumber', 'Timestamp', 'Price_Model3_sim']],
    on=['SystemCodeNumber', 'Timestamp'],
    how='left'
)

# Sort data by lot and timestamp for plotting
comparison_sim_df = comparison_sim_df.sort_values(by=["SystemCodeNumber", "Timestamp"])

# Get list of all unique parking lots
parking_lots_sim = comparison_sim_df['SystemCodeNumber'].unique()

# Prepare a list to hold plots for each parking lot
plots_sim = []

# Generate and add a plot for each parking lot
for lot in parking_lots_sim:
    lot_df_sim = comparison_sim_df[comparison_sim_df['SystemCodeNumber'] == lot].dropna(subset=['Price_Model1_sim', 'Price_Model2_sim', 'Price_Model3_sim'])

    if lot_df_sim.empty:
        print(f"No complete price data for lot: {lot}. Skipping plot.")
        continue

    # Use ColumnDataSource for better performance with Bokeh
    source_sim = ColumnDataSource(lot_df_sim)

    # Create a new figure for the current parking lot
    p_sim = figure(
        title=f"Simulated Price Comparison for Lot: {lot}",
        x_axis_label='Time',
        y_axis_label='Price ($)',
        x_axis_type='datetime',
        width=800,
        height=300,
        tools="pan,wheel_zoom,box_zoom,reset,save" # Add interactive tools
    )

    # Add lines for Model 1, Model 2, and Model 3 simulated prices
    l1_sim = p_sim.line(x='Timestamp', y='Price_Model1_sim', source=source_sim, color='green', line_width=2, legend_label='Model 1')
    l2_sim = p_sim.line(x='Timestamp', y='Price_Model2_sim', source=source_sim, color='blue', line_width=2, legend_label='Model 2')
    l3_sim = p_sim.line(x='Timestamp', y='Price_Model3_sim', source=source_sim, color='red', line_width=2, legend_label='Model 3')


    # Configure legend
    p_sim.legend.location = "top_left"
    p_sim.legend.click_policy = "hide" # Allows toggling lines by clicking legend

    # Add the plot to the list
    plots_sim.append(p_sim)

# Show all plots vertically stacked
show(column(*plots_sim))

* * *
### Analyze the Impact of Parameters on Pricing Models
* * *

This section would involve exploring how changing the parameters in Model 1 and Model 2 affects the resulting prices. This typically requires rerunning the simulations with different parameter values and observing the changes.

*Note: Due to the nature of this analysis requiring multiple simulation runs with parameter variations, a single static code cell cannot fully demonstrate this. Below is an example of how you might structure code to explore the impact of a single parameter (e.g., ALPHA_SIM_M1 in Model 1).*

In [37]:
# Example: Analyze the impact of ALPHA_SIM_M1 on Model 1 prices

# Define a range of ALPHA_SIM_M1 values to test
alpha_values = [1.0, 5.0, 10.0] # Example values

results = {}

for alpha in alpha_values:
    # Recalculate Model 1 price with the current alpha value
    price_model1_alpha = BASE_PRICE_SIM_M1 + alpha * df['OccupancyRatio_sim_M1']
    results[f'Price_Model1_Alpha_{alpha}'] = price_model1_alpha

# Create a DataFrame to compare prices for different alpha values
alpha_impact_df = df[['SystemCodeNumber', 'Timestamp', 'OccupancyRatio_sim_M1']].copy()
for col, data in results.items():
    alpha_impact_df[col] = data

print("📈 Impact of ALPHA_SIM_M1 on Model 1 Price:")
display(alpha_impact_df.head())

# Further analysis could involve plotting these results for a specific parking lot
# or calculating summary statistics for each alpha value.

# Example: Plot for a single lot to visualize the impact
lot_to_plot = df['SystemCodeNumber'].iloc[0] # Select the first lot for demonstration
lot_alpha_df = alpha_impact_df[alpha_impact_df['SystemCodeNumber'] == lot_to_plot]

if not lot_alpha_df.empty:
    p_alpha = figure(
        title=f"Impact of Alpha on Model 1 Price for Lot: {lot_to_plot}",
        x_axis_label='Time',
        y_axis_label='Price ($)',
        x_axis_type='datetime',
        width=800,
        height=300,
        tools="pan,wheel_zoom,box_zoom,reset,save"
    )

    colors = Category10[len(alpha_values)]
    for i, alpha in enumerate(alpha_values):
        p_alpha.line(x='Timestamp', y=f'Price_Model1_Alpha_{alpha}', source=ColumnDataSource(lot_alpha_df), color=colors[i], line_width=2, legend_label=f'Alpha = {alpha}')

    p_alpha.legend.location = "top_left"
    p_alpha.legend.click_policy = "hide"
    show(p_alpha)
else:
    print(f"No data found for lot {lot_to_plot} to plot alpha impact.")

📈 Impact of ALPHA_SIM_M1 on Model 1 Price:


SystemCodeNumber           Timestamp  OccupancyRatio_sim_M1  \
0      BHMBCCMKT01 2016-10-04 07:59:00               0.105719   
1      BHMNCPHST01 2016-10-04 07:59:00               0.197500   
2      BHMMBMMBX01 2016-10-04 07:59:00               0.384279   
3      BHMNCPNST01 2016-10-04 07:59:00               0.513402   
4         Shopping 2016-10-04 07:59:00               0.319792   

   Price_Model1_Alpha_1.0  Price_Model1_Alpha_5.0  Price_Model1_Alpha_10.0  
0               10.105719               10.528596                11.057192  
1               10.197500               10.987500                11.975000  
2               10.384279               11.921397                13.842795  
3               10.513402               12.567010                15.134021  
4               10.319792               11.598958                13.197917

* * *
### Visualize Price Distributions (Simulated Data)
* * *

Generate plots (e.g., histograms or box plots) to visualize the distribution of simulated prices for each model.

In [40]:
from bokeh.transform import factor_cmap
from bokeh.models import FactorRange
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource
from bokeh.palettes import Category10
import pandas as pd # Ensure pandas is imported

# Prepare data for plotting simulated price distributions
# We'll use the merged comparison_sim_df DataFrame
price_distribution_sim_df = comparison_sim_df[['Price_Model1_sim', 'Price_Model2_sim', 'Price_Model3_sim']].melt(var_name='Model', value_name='Price')

# Clean up model names for better labels
price_distribution_sim_df['Model'] = price_distribution_sim_df['Model'].str.replace('_sim', '').str.replace('Price_', '')

# Create a list of models for the x-axis
models_sim = ['Model1', 'Model2', 'Model3']

# Create a ColumnDataSource from the melted DataFrame
source_sim_dist = ColumnDataSource(price_distribution_sim_df)

# Create a figure for the price distribution
p_sim_dist = figure(
    x_range=FactorRange(*models_sim),
    title="Simulated Price Distribution by Model",
    x_axis_label="Pricing Model",
    y_axis_label="Price ($)",
    height=300,
    tools="pan,wheel_zoom,box_zoom,reset,save"
)

# Calculate quartiles, IQR, and outliers for each model for box plots
grouped_sim = price_distribution_sim_df.groupby('Model')['Price']
q1_sim = grouped_sim.quantile(q=0.25)
q2_sim = grouped_sim.quantile(q=0.5) # median
q3_sim = grouped_sim.quantile(q=0.75)
iqr_sim = q3_sim - q1_sim
upper_outliers_sim = q3_sim + 1.5 * iqr_sim
lower_outliers_sim = q1_sim - 1.5 * iqr_sim

# Create a new dataframe for box plot data
box_plot_data_sim = pd.DataFrame({
    'Model': models_sim,
    'q1': q1_sim.loc[models_sim].values,
    'q2': q2_sim.loc[models_sim].values,
    'q3': q3_sim.loc[models_sim].values,
    'iqr': iqr_sim.loc[models_sim].values,
    'upper': q3_sim.loc[models_sim].values + 1.5*iqr_sim.loc[models_sim].values,
    'lower': q1_sim.loc[models_sim].values - 1.5*iqr_sim.loc[models_sim].values
})

# Draw the box and whiskers
# Whiskers
p_sim_dist.segment(x0='Model', y0='upper', x1='Model', y1='q3', source=ColumnDataSource(box_plot_data_sim), line_color="black")
p_sim_dist.segment(x0='Model', y0='lower', x1='Model', y1='q1', source=ColumnDataSource(box_plot_data_sim), line_color="black")

# Boxes
p_sim_dist.vbar(x='Model', top='q3', bottom='q2', width=0.7, source=ColumnDataSource(box_plot_data_sim), line_color="black", fill_color=factor_cmap('Model', palette=Category10[3], factors=models_sim))
p_sim_dist.vbar(x='Model', top='q2', bottom='q1', width=0.7, source=ColumnDataSource(box_plot_data_sim), line_color="black", fill_color=factor_cmap('Model', palette=Category10[3], factors=models_sim))

# Outliers (optional) - need to filter outliers from the original data
def identify_outliers_sim(group):
    q1 = group.quantile(0.25)
    q3 = group.quantile(0.75)
    iqr = q3 - q1
    upper = q3 + 1.5 * iqr
    lower = q1 - 1.5 * iqr
    return group[(group > upper) | (group < lower)]

outliers_sim = price_distribution_sim_df.groupby('Model')['Price'].apply(identify_outliers_sim).reset_index()
if not outliers_sim.empty:
    p_sim_dist.scatter(x='Model', y='Price', source=ColumnDataSource(outliers_sim), size=6, color="black", alpha=0.6)


# Customize appearance
p_sim_dist.xgrid.grid_line_color = None
p_sim_dist.y_range.start = 0

# Show the plot
show(p_sim_dist)

* * *
### Revenue Comparison
* * *

Calculate the total revenue generated by each simulated pricing model over the dataset's time period.

In [42]:

if 'Occupancy' not in comparison_sim_df.columns:
    comparison_sim_df = comparison_sim_df.merge(
        df[['SystemCodeNumber', 'Timestamp', 'Occupancy']],
        on=['SystemCodeNumber', 'Timestamp'],
        how='left'
    )


comparison_sim_df['Revenue_Model1_sim'] = comparison_sim_df['Price_Model1_sim'] * comparison_sim_df['Occupancy']
comparison_sim_df['Revenue_Model2_sim'] = comparison_sim_df['Price_Model2_sim'] * comparison_sim_df['Occupancy']
comparison_sim_df['Revenue_Model3_sim'] = comparison_sim_df['Price_Model3_sim'] * comparison_sim_df['Occupancy']


total_revenue_model1 = comparison_sim_df['Revenue_Model1_sim'].sum()
total_revenue_model2 = comparison_sim_df['Revenue_Model2_sim'].sum()
total_revenue_model3 = comparison_sim_df['Price_Model3_sim'] * comparison_sim_df['Occupancy']

print("💰 Total Simulated Revenue Comparison:")
print(f"Model 1 (Simple Occupancy): ${total_revenue_model1:,.2f}")
print(f"Model 2 (Feature-Rich Demand): ${total_revenue_model2:,.2f}")
print(f"Model 3 (Competitive Pricing): ${total_revenue_model3.sum():,.2f}")


average_revenue_per_lot = comparison_sim_df.groupby('SystemCodeNumber')[['Revenue_Model1_sim', 'Revenue_Model2_sim', 'Revenue_Model3_sim']].mean().round(2)
print("\nAverage Simulated Revenue Per Parking Lot ($):")
display(average_revenue_per_lot)



💰 Total Simulated Revenue Comparison:
Model 1 (Simple Occupancy): $181,320,412.66
Model 2 (Feature-Rich Demand): $191,890,298.15
Model 3 (Competitive Pricing): $196,130,241.16

Average Simulated Revenue Per Parking Lot ($):


Revenue_Model1_sim  Revenue_Model2_sim  Revenue_Model3_sim
SystemCodeNumber                                                            
BHMBCCMKT01                  1809.48             2176.20             2206.38
BHMBCCTHL01                  3810.76             3697.24             3779.66
BHMEURBRD01                  3891.91             3994.74             3964.27
BHMMBMMBX01                  6312.92             6092.73             6092.73
BHMNCPHST01                  6093.07             6668.88             6777.37
BHMNCPNST01                  3355.71             3282.33             3379.37
Broad Street                 5617.64             5596.60             5634.50
Others-CCCPS105a            14238.52            14769.93            15193.25
Others-CCCPS119a             5630.79             6869.71             7067.82
Others-CCCPS135a            28849.91            29357.79            30113.05
Others-CCCPS202             11429.95            13172.01            13430.88
Others-CCCPS8                8038.81             8539.66             8783.23
Others-CCCPS98              11526.79            13035.73            13460.62
Shopping                    13179.19            13881.17            14141.79

* * *
### Conclusion
* * *

This notebook explored three dynamic parking pricing models: a simple occupancy-based model (Model 1), a feature-rich demand model (Model 2), and a competitive pricing model (Model 3). The analysis and simulation of these models using the provided dataset revealed significant differences in their pricing behavior and revenue generation potential.

**Key Observations and Results:**

1.  **Model Complexity and Price Dynamics:**
    *   **Model 1 (Simple Occupancy):** This model generates the least dynamic prices, primarily responding only to changes in occupancy. Its price range is the narrowest, and the price fluctuations are less pronounced compared to the other models. This simplicity makes it easy to understand and implement but limits its ability to capture complex demand patterns.
    *   **Model 2 (Feature-Rich Demand):** By incorporating additional factors such as queue length, traffic conditions, special days, and vehicle type, Model 2 produces more dynamic prices. The prices in this model are more responsive to a wider set of real-time conditions, leading to greater price variability and a wider price distribution than Model 1.
    *   **Model 3 (Competitive Pricing):** Building on Model 2, this model further refines pricing by considering the average price of nearby competitors. This introduces an external factor into the pricing decision, aiming to make prices more strategic in a competitive landscape. The price dynamics in Model 3 are similar to Model 2 but show subtle adjustments based on the competitive environment.

2.  **Revenue Performance:**
    *   The simulation results clearly demonstrate a hierarchy in revenue generation among the models.
    *   **Model 1** yields the lowest total revenue, which is expected given its limited responsiveness to diverse demand indicators.
    *   **Model 2** generates significantly higher total revenue than Model 1. This highlights the value of integrating more relevant features to better estimate demand and adjust prices accordingly.
    *   **Model 3** achieves the highest total revenue among the three models. The competitive pricing adjustments, while seemingly small in individual instances, collectively contribute to an uplift in overall revenue. This suggests that being mindful of competitor pricing is a valuable component of a dynamic pricing strategy.
    *   The analysis of average revenue per parking lot also reinforces these findings, showing that, on average, Model 2 and Model 3 generate more revenue per lot than Model 1.

3.  **Impact of Parameters:**
    *   The example analysis of the `ALPHA_SIM_M1` parameter in Model 1 demonstrated how sensitive the pricing model is to changes in its parameters. Increasing the `ALPHA` value amplifies the impact of occupancy on price, leading to larger price swings and potentially higher peak prices when occupancy is high. This underscores the importance of carefully tuning model parameters based on desired pricing objectives and market characteristics. Similar sensitivity would be observed with parameters in Model 2 and Model 3.

**Overall Takeaways:**

*   Dynamic pricing models that consider a broader range of demand factors (like Model 2) are likely to be more effective in capturing the true demand for parking and generating higher revenue than simpler models based solely on occupancy.
*   Incorporating competitive analysis into dynamic pricing (like Model 3) can provide an additional layer of optimization, potentially leading to further revenue gains by strategically positioning prices relative to competitors.
*   The choice of model and the tuning of its parameters are critical for success. Organizations should carefully consider the available data, the competitive landscape, and their revenue goals when selecting and configuring a dynamic pricing strategy.

This analysis provides a foundational understanding of how different dynamic pricing models perform. Further work could involve more sophisticated modeling techniques, including machine learning, real-time data processing pipelines, and more detailed competitive analysis, to develop even more optimized pricing strategies.

## Summary:

### Data Analysis Key Findings

*   The project analyzes and simulates three dynamic parking pricing models: simple occupancy, feature-rich demand, and competitive pricing.
*   The project utilizes Python, pandas, NumPy, Bokeh, Pathway, and Matplotlib in its tech stack.
*   The workflow involves data loading and processing, distance calculation, simulating three different pricing models, comparing price outputs, performing analysis and visualization, calculating and comparing simulated revenues, and conducting a separate Pathway simulation for real-time data processing.
*   A Mermaid diagram is used to visualize the project's architecture and workflow, showing the flow from raw data through different models, analysis, visualization, and simulation components.

### Insights or Next Steps

*   The README provides a solid foundation for understanding the project. Consider adding a section on potential future enhancements or areas for further research, such as incorporating machine learning models for demand prediction or exploring different competitive pricing strategies.
*   Including examples of the visualizations generated by the project directly in the README would enhance its appeal and provide immediate insight into the project's output.
